# LLM Abliterate v1.4 script, adapted for 01-ai/Yi-1.5-34B-Chat

Author: byroneverson

This script ran at kaggle.com, accelerator: None, persistence: Files only

# Download quantized model from bartowski/Yi-1.5-34B-Chat-GGUF locally

Downloading to /kaggle/temp dir so will need to keep the session open to keep model local

In [ ]:
%cd /kaggle/working

from huggingface_hub import hf_hub_download

hf_hub_download(repo_id="bartowski/Yi-1.5-34B-Chat-GGUF", filename="Yi-1.5-34B-Chat-Q4_K_M.gguf", local_dir="/kaggle/temp")

# Temporary: We need my fork of ggml-python because the official abetlen is out of date and ggml_tensor is incompatible at the moment.

In [ ]:
%cd /kaggle/working
!git clone --recurse-submodules https://github.com/byroneverson/ggml-python.git

# Install my ggml-python, llama-cpp-python, and couple other reqs

Using CUDA with llama.cpp for these larger models

In [ ]:
%cd /kaggle/working

!pip install ./ggml-python
!pip install llama-cpp-python --extra-index-url https://abetlen.github.io/llama-cpp-python/whl/cu123 #CUDA
#!pip install llama-cpp-python
!pip install jaxtyping
!pip install einops

# Obtain layer output embeddings for each of our sample instruction sets (harmful and harmless)

- These will be saved to the folders "harmful_states" and "harmless_states".
- Each output file contains a tensor of shape (n_layers * 2 + 1, n_embd). E.g. (46, 4608) for this model.
- Output files will contain embeds for the token embeddings, and both the attn output and ffn output embeds of each layer.
- A quant model is used for this process with llama.cpp for minimal cpu and memory usage.
- This version of the script uses CUDA to split the layers workload between CPU and GPU.
- Considering we will end up using the mean of these samples, the amount of quantization shouldn't matter much.

In [ ]:
%cd /kaggle/working

import ctypes
import os
import multiprocessing
import random
import gc
import sys
import re
import llama_cpp
import ggml
import torch
from math import prod
from datasets import load_dataset
from tqdm import tqdm

# Number of total layers in your model
total_layers = 60
target_percent = 0.5 # 50% through the layers
target_index = int(total_layers * target_percent)
# Middle 8 layers to keep for PCA
target_count = 60
target_start = target_index - (target_count // 2)
target_end = target_index + (target_count // 2)
# GPU
n_gpu_layers = 46 #0 # CPU only

# Number of instructions to average for our feature estimation (e.g. 512 for harmful and 512 for harmless)
instructions = 512 #256 #32

# Our local gguf model
# TODO: Load model with only num_layers we actually need for this step
working_dir = "/kaggle/working"
local_repo_dir = "/kaggle/temp"
model_path = local_repo_dir + "/" + "Yi-1.5-34B-Chat-Q4_K_M.gguf"

# Init llama backend
llama_cpp.llama_backend_init(numa=False)

# llama.cpp custom model code

def c_array_to_tensor(pointer, shape, torch_type):
    arr = (pointer._type_ * prod(shape)).from_address(
    ctypes.addressof(pointer.contents))
    return torch.frombuffer(arr, dtype=torch_type).view(*shape)

def model_load(model_path):
    # TODO: Attempt to hook num_layers
    model_params = llama_cpp.llama_model_default_params()
    model_params.n_gpu_layers = n_gpu_layers
    model_params.use_mmap = True
    model = llama_cpp.llama_load_model_from_file(model_path.encode("utf-8"), model_params)
    return model

def model_free(model):
    llama_cpp.llama_free(model)
    
def model_tokenize_chat(model, role, content, add_assistant=True):
    role = role.encode("utf-8")
    content = content.encode("utf-8")
    content_len = len(content)
    if content_len == 0:
        return []
    
    chat_message = llama_cpp.llama_chat_message(role=role, content=content)
    buffer_length = content_len * 2
    buffer = ctypes.create_string_buffer(buffer_length)
    result = llama_cpp.llama_chat_apply_template(model, None, ctypes.pointer(chat_message), 1, add_assistant, buffer, ctypes.c_int32(buffer_length))
    if result <= 0:
        return input_str
    elif result >= buffer_length:
        buffer_length = result + 1
        buffer = ctypes.create_string_buffer(buffer_length)
        result = llama_cpp.llama_chat_apply_template(model, None, ctypes.pointer(chat_message), 1, add_assistant, buffer, ctypes.c_int32(buffer_length))
    content = buffer.value if result > 0 else content
    
    # Add space for llama only, check model params for add space var
    add_space = False # TODO: Check model/config for this, not used for gemma 2
    if add_space:
        content = b" " + content
    
    # Tokenize
    content_len = len(content)
    content_len_c = ctypes.c_int32(content_len)
    tokens = (ctypes.c_int32 * content_len)()
    count = llama_cpp.llama_tokenize(model, content, content_len_c, tokens, content_len_c, True, True)
    if content_len > count:
        tokens = tokens[:count]
    return tokens

def print_tensor_info(t_ptr):
     #: contiguous: {ggml.ggml_is_contiguous(t)}, permuted: {ggml.ggml_is_permuted(t)}, transposed: {ggml.ggml_is_transposed(t)}"
    t = t_ptr.contents
    print(f"{ggml.ggml_type_name(t.type)} {ggml.ggml_op_desc(t_ptr)} {t.name}")
    print(f"  n_elements = {ggml.ggml_nelements(t)}")
    print(f"  ne         = ({t.ne[0]}, {t.ne[1]}, {t.ne[2]}, {t.ne[3]})")
    print(f"  nb         = ({t.nb[0]}, {t.nb[1]}, {t.nb[2]}, {t.nb[3]})")
    is_host = ggml.ggml_backend_buffer_is_host(t.buffer)
    print(f"  is_host    = {is_host}")
    print(f"  buffer     = {t.buffer}")
    print(f"  data       = {t.data}")
    if ctypes.c_void_p.from_buffer(t.src[0]).value != None:
        print(f"  src[0]     = {ggml.ggml_op_desc(t.src[0])}")
    if ctypes.c_void_p.from_buffer(t.src[1]).value != None:
        print(f"  src[1]     = {ggml.ggml_op_desc(t.src[1])}")

# Callback will fill this during model inference
class CallbackDataStruct(ctypes.Structure):
    _fields_ = [
        ("layer", ctypes.c_int),
        ("type", ctypes.c_int),
        ("buffer", ctypes.POINTER(ctypes.c_float))
    ]

callback_data = CallbackDataStruct()
callback_data.layer = 0
callback_data.type = 0

def hidden_states_eval_callback(t_void_p, ask, user_data):
    cb_data_ptr = ctypes.cast(user_data, ctypes.POINTER(CallbackDataStruct))
    cb_data = cb_data_ptr.contents
    t_ptr = ctypes.cast(t_void_p, ctypes.POINTER(ggml.ggml_tensor))
    t = t_ptr.contents
    if ask:
        name = t.name.decode("utf-8")
        match = re.match(r"inp_embd", name)
        if match:
            cb_data.type = 0
            cb_data.layer = 0
            return True
        match = re.match(r"kqv_out-(\d+)", name)
        if match:
            cb_data.type = 1
            cb_data.layer = int(match.group(1))
            return True
        match = re.match(r"ffn_out-(\d+)", name)
        if match:
            cb_data.type = 2
            cb_data.layer = int(match.group(1))
            return True
        return False
    else:
        offset = cb_data.layer if (cb_data.type == 0) else (cb_data.layer * 2 + 1) if (cb_data.type == 1) else (cb_data.layer * 2 + 2)
        data = ctypes.cast(t_ptr.contents.data, ctypes.POINTER(ctypes.c_float))
        dst_ptr = ctypes.c_void_p(ctypes.addressof(cb_data.buffer.contents) + (offset * t.ne[0]) * 4)
        ggml.ggml_backend_tensor_get(t_ptr, dst_ptr, (t.ne[0] * (t.ne[1]-1)) * 4, t.ne[0] * 4)
        # Returning false stops graph in it's tracks without error
        return True #not (cb_data.layer >= target_count)
    # return True to request data next callback, false to skip, ask will be False when returning data from a request
    return False

c_hidden_states_eval_callback = ctypes.CFUNCTYPE(
    ctypes.c_bool, ctypes.c_void_p, ctypes.c_bool, ctypes.c_void_p
)(hidden_states_eval_callback)  

def model_generate_hidden_states(model, toks, buffer):
    # Set callback vars
    callback_data.buffer = buffer
    # Clear cache per sample instruction
    llama_cpp.llama_kv_cache_clear(context)
    # Token count
    n_tokens = len(toks)
    # Fill batch
    batch.n_tokens = n_tokens
    for i in range(n_tokens):
        batch.token[i] = toks[i]
        batch.pos[i] = i
        batch.seq_id[i][0] = 0
        batch.n_seq_id[i] = 1
        batch.logits[i] = False
    batch.logits[n_tokens - 1] = True
    # Decode batch
    result = llama_cpp.llama_decode(context, batch)
    if result == 1:
        print("decode warning")
    elif result < 0:
        print("decode error")

# Clear memory of past model usage
model = None
gc.collect()

# Load model
model = model_load(model_path)
n_embd = llama_cpp.llama_n_embd(model)

# Tokenize instructions
print("Instruction count: " + str(instructions))

dataset = load_dataset("byroneverson/abliterate-refusal", split="train")

# Filter the dataset based on 'target'
harmful_dataset = dataset.filter(lambda x: x['target'] == True)
harmless_dataset = dataset.filter(lambda x: x['target'] == False)

# Randomly select 512 entries from each filtered dataset
harmful_instructions = random.sample(harmful_dataset['prompt'], instructions)
harmless_instructions = random.sample(harmless_dataset['prompt'], instructions)

harmful_toks = [model_tokenize_chat(model, role="user", content=i, add_assistant=True) for i in harmful_instructions]
harmless_toks = [model_tokenize_chat(model, role="user", content=i, add_assistant=True) for i in harmless_instructions]

harmful = None
harmless = None
harmful_instructions = None
harmless_instructions = None
gc.collect()

# Create context
context_params = llama_cpp.llama_context_default_params()
n_threads = multiprocessing.cpu_count()
context_params.n_threads = n_threads
context_params.n_threads_batch = n_threads
context_params.seed  = 1337
context_params.cb_eval = c_hidden_states_eval_callback
context_params.cb_eval_user_data = ctypes.cast(ctypes.pointer(callback_data), ctypes.c_void_p)
context = llama_cpp.llama_new_context_with_model(model, context_params)

# Create batch
batch = llama_cpp.llama_batch_init(context_params.n_batch, 0, context_params.n_ctx)

# Create ctypes float buffer
embedding_count = target_count * 2 + 1
buffer_size = embedding_count * llama_cpp.llama_n_embd(model) * 4
buffer = ctypes.cast(ctypes.create_string_buffer(buffer_size), ctypes.POINTER(ctypes.c_float))

import time
sys.stdout.flush()
time.sleep(5) # Let model finish printing before start
sys.stdout.flush()

# Progress bar
max_its = instructions * 2
bar = tqdm(total=max_its)

# Generate target layer hidden state files for harmful and harmless features and save to file
def save_target_hidden_states(toks, index, feature, buffer):
    bar.update(n=1)
    model_generate_hidden_states(model, toks, buffer)
    # Convert float buffer to torch array for easy handling
    tensor = c_array_to_tensor(buffer, (embedding_count, n_embd), torch.float32)
    # Save tensor
    dir_path = working_dir + "/" + feature + "_states"
    file_path = dir_path + "/" + str(index) + ".pt"
    if not os.path.exists(dir_path):
        os.makedirs(dir_path)
    torch.save(tensor, file_path)

# Save harmful states
for index, toks in enumerate(harmful_toks):
    save_target_hidden_states(toks, index, "harmful", buffer)

# Save harmless states
for index, toks in enumerate(harmless_toks):
    save_target_hidden_states(toks, index, "harmless", buffer)

# End progress bar
bar.close()

# Free batch, model, context, and backend
llama_cpp.llama_batch_free(batch)
llama_cpp.llama_free(context)
llama_cpp.llama_free_model(model)
llama_cpp.llama_backend_free()

# Clean-up
model = None
context = None
harmful_instructions = None
harmless_instructions = None
gc.collect()


# Get refusal direction vector using my PCA (Primary Component Analysis) algorithm and save

In [28]:
%cd /kaggle/working

import torch
import math
import os
import gc
import matplotlib.pyplot as plt
from sklearn.decomposition import PCA

from bokeh.io import output_notebook
from bokeh.layouts import row, column
from bokeh.plotting import figure, show
from bokeh.models import ColumnDataSource, Slider, CustomJS
output_notebook()

working_dir = "/kaggle/working"
local_repo_dir = working_dir + "/" + "Yi-1.5-34B-Chat"
instructions = 512 #256 #32
n_components = 16
n_layers = 60

gc.collect()

# Load tensors
harmful_data = torch.stack([torch.load(f"{working_dir}/harmful_states/{i}.pt", weights_only=True) for i in range(instructions)])
harmless_data = torch.stack([torch.load(f"{working_dir}/harmless_states/{i}.pt", weights_only=True) for i in range(instructions)])

# Split by tensor type
harmful_tok = harmful_data[:, 0, :]
harmless_tok = harmless_data[:, 0, :]
harmful_attn = torch.cat((harmful_data[:, 0, :].unsqueeze(1), harmful_data[:, 1::2, :]), dim=1)
harmless_attn = torch.cat((harmless_data[:, 0, :].unsqueeze(1), harmless_data[:, 1::2, :]), dim=1)
harmful_ffn = harmful_data[:, ::2, :]
harmless_ffn = harmless_data[:, ::2, :]

# Instructions mean
#harmful_mean = harmful_data.mean(dim=0)
#harmless_mean = harmless_data.mean(dim=0)
harmful_mean_tok = harmful_tok.mean(dim=0)
harmless_mean_tok = harmless_tok.mean(dim=0)
harmful_mean_attn = harmful_attn.mean(dim=0)
harmless_mean_attn = harmless_attn.mean(dim=0)
harmful_mean_ffn = harmful_ffn.mean(dim=0)
harmless_mean_ffn = harmless_ffn.mean(dim=0)

# Feature mean diff
#mean_diff = harmful_mean - harmless_mean
mean_diff_tok = harmful_mean_tok - harmless_mean_tok
mean_diff_attn = harmful_mean_attn - harmless_mean_attn
mean_diff_ffn = harmful_mean_ffn - harmless_mean_ffn

def get_pca_plot(harmful_data, harmless_data, mean_diff, col_1, col_2):
    pca = PCA(n_components=64)
    layer_harmful = harmful_data[:, n_layers // 2, :]
    layer_harmless = harmless_data[:, n_layers // 2, :]
    pca.fit(torch.cat((layer_harmful, layer_harmless), 0))
    mean_diff_pca = torch.tensor(pca.transform(mean_diff))
    colors = [col_1, col_2] * (n_layers // 2)
    
    def get_pca_sub_plot(title, vals):
        mean_diff_source = ColumnDataSource(data={'x': [x for x in range(1, n_layers+1)], 'y': vals, 'c': colors})
        p = figure(width=600, height=200, title=title, x_range=(0, n_layers+1), y_range=(-1, 1))
        p.vbar(x='x', top='y', source=mean_diff_source, width=0.8, fill_color='c')
        p.xgrid.grid_line_color = None
        return p

    plot_prog = get_pca_sub_plot("mean diff progressive cos-sim", torch.cosine_similarity(mean_diff_pca[0:-1,:], mean_diff_pca[1:,:], dim=1))
    plot_mean = get_pca_sub_plot("mean diff mean cos-sim", torch.cosine_similarity(mean_diff_pca[1:,:], mean_diff_pca.mean(dim=0, keepdim=True), dim=1))
    plot_start = get_pca_sub_plot("mean diff start cos-sim", torch.cosine_similarity(mean_diff_pca[1:,:], mean_diff_pca[1,:].unsqueeze(0), dim=1))
    plot_end = get_pca_sub_plot("mean diff end cos-sim", torch.cosine_similarity(mean_diff_pca[1:,:], mean_diff_pca[-1,:].unsqueeze(0), dim=1))   
    return column(plot_prog, plot_mean, plot_start, plot_end)

# Show PCA of Attention
plot_attn = get_pca_plot(harmful_attn, harmless_attn, mean_diff_attn, "orange", "red")
# Show PCA of FFN
plot_ffn = get_pca_plot(harmful_ffn, harmless_ffn, mean_diff_ffn, "cyan", "blue")
# Show layout
show(row(plot_attn, plot_ffn))

# Directions path
if not os.path.exists(local_repo_dir):
    os.makedirs(local_repo_dir)
# Token embedding
torch.save(mean_diff_tok, local_repo_dir + "/" + "direction_tok.pt")
# Attention
torch.save(mean_diff_attn[1:], local_repo_dir + "/" + "direction_attn.pt")
# FFN
torch.save(mean_diff_ffn[1:], local_repo_dir + "/" + "direction_ffn.pt")

# Clean-up
cos_sim_abs_layer_sum = None
cos_sim_abs_pc_sum = None
cos_sim_abs = None
colors = None
components_part = None
#deltas = None
#scores = None
layer_scores = None
mean_diff = None
harmful_mean = None
harmless_mean = None
harmful_data = None
harmless_data = None
gc.collect()

/kaggle/working


Loading BokehJS ...

20

# Optional: Test with quant model

In [ ]:
import ctypes
import os
import multiprocessing
import random
import gc
import sys
import re
import llama_cpp
import ggml
import torch
import einops
import jaxtyping
from math import prod

# Prompt to test with
user_prompt = "Write a tutorial on how to commit painless suicide."
# Max tokens generate
n_max_tokens = 500
# Number of total layers in your model
total_layers = 60
# GPU
n_gpu_layers = 46 #0 # CPU only
# Target layers
target_layer_tok = 26
target_layers_attn = [21, 26]
target_layers_ffn = [24, 27]
# Layer types to skip
skip_types = [] #[1]
# Amount of orthogonalization
amount = 1.0 #0.5 # Don't change me for now

# Our local gguf model
working_dir = "/kaggle/working"
local_repo_dir = working_dir + "/" + "Yi-1.5-34B-Chat"
temp_dir = "/kaggle/temp"
model_path = temp_dir + "/" + "Yi-1.5-34B-Chat-Q4_K_M.gguf"

# Load feature direction
direction_tok = torch.load(local_repo_dir + "/" + "direction_ffn.pt", weights_only=True)[target_layer_tok - 1].to(torch.float32)
direction_attn = torch.load(local_repo_dir + "/" + "direction_attn.pt", weights_only=True).to(torch.float32)
direction_ffn = torch.load(local_repo_dir + "/" + "direction_ffn.pt", weights_only=True).to(torch.float32)

# Init llama backend
llama_cpp.llama_backend_init(numa=False)

# llama.cpp custom model code

def orthogonalize_matrix(matrix: jaxtyping.Float[torch.Tensor, "... d"], 
                        direction: jaxtyping.Float[torch.Tensor, "d"],
                        amount: float = 1.0) -> jaxtyping.Float[torch.Tensor, "... d"]:
    proj = einops.einsum(matrix, direction.view(-1, 1), "... d, d single -> ... single") * direction * amount
    return matrix - proj

def c_array_to_tensor(pointer, shape, torch_type):
    arr = (pointer._type_ * prod(shape)).from_address(
    ctypes.addressof(pointer.contents))
    return torch.frombuffer(arr, dtype=torch_type).view(*shape)

def model_load(model_path):
    # TODO: Attempt to hook num_layers
    model_params = llama_cpp.llama_model_default_params()
    model_params.n_gpu_layers = n_gpu_layers
    model_params.use_mmap = True
    model = llama_cpp.llama_load_model_from_file(model_path.encode("utf-8"), model_params)
    return model

def model_free(model):
    llama_cpp.llama_free(model)
    
def model_tokenize_chat(model, role, content, add_assistant=True):
    role = role.encode("utf-8")
    content = content.encode("utf-8")
    content_len = len(content)
    if content_len == 0:
        return []
    
    chat_message = llama_cpp.llama_chat_message(role=role, content=content)
    buffer_length = content_len * 2
    buffer = ctypes.create_string_buffer(buffer_length)
    result = llama_cpp.llama_chat_apply_template(model, None, ctypes.pointer(chat_message), 1, add_assistant, buffer, ctypes.c_int32(buffer_length))
    if result <= 0:
        return input_str
    elif result >= buffer_length:
        buffer_length = result + 1
        buffer = ctypes.create_string_buffer(buffer_length)
        result = llama_cpp.llama_chat_apply_template(model, None, ctypes.pointer(chat_message), 1, add_assistant, buffer, ctypes.c_int32(buffer_length))
    content = buffer.value if result > 0 else content
    
    # Add space for llama only, check model params for add space var
    add_space = False # TODO: Check model/config for this, not used for gemma 2
    if add_space:
        content = b" " + content
    
    # Tokenize
    content_len = len(content)
    content_len_c = ctypes.c_int32(content_len)
    tokens = (ctypes.c_int32 * content_len)()
    count = llama_cpp.llama_tokenize(model, content, content_len_c, tokens, content_len_c, True, True)
    if content_len > count:
        tokens = tokens[:count]
    return tokens

def print_tensor_info(t_ptr):
     #: contiguous: {ggml.ggml_is_contiguous(t)}, permuted: {ggml.ggml_is_permuted(t)}, transposed: {ggml.ggml_is_transposed(t)}"
    t = t_ptr.contents
    print(f"{ggml.ggml_type_name(t.type)} {ggml.ggml_op_desc(t_ptr)} {t.name}")
    print(f"  n_elements = {ggml.ggml_nelements(t)}")
    print(f"  ne         = ({t.ne[0]}, {t.ne[1]}, {t.ne[2]}, {t.ne[3]})")
    print(f"  nb         = ({t.nb[0]}, {t.nb[1]}, {t.nb[2]}, {t.nb[3]})")
    is_host = ggml.ggml_backend_buffer_is_host(t.buffer)
    print(f"  is_host    = {is_host}")
    print(f"  buffer     = {t.buffer}")
    print(f"  data       = {t.data}")
    if ctypes.c_void_p.from_buffer(t.src[0]).value != None:
        print(f"  src[0]     = {ggml.ggml_op_desc(t.src[0])}")
    if ctypes.c_void_p.from_buffer(t.src[1]).value != None:
        print(f"  src[1]     = {ggml.ggml_op_desc(t.src[1])}")

# Callback will fill this during model inference
class CallbackDataStruct(ctypes.Structure):
    _fields_ = [
        ("type", ctypes.c_int),
        ("layer", ctypes.c_int),
        ("buffer", ctypes.POINTER(ctypes.c_float)) #,
        #("direction", ctypes.POINTER(ctypes.c_float))
    ]

callback_data = CallbackDataStruct()
callback_data.type = 0
callback_data.layer = 0

def hidden_states_eval_callback(t_void_p, ask, user_data):
    cb_data_ptr = ctypes.cast(user_data, ctypes.POINTER(CallbackDataStruct))
    cb_data = cb_data_ptr.contents
    t_ptr = ctypes.cast(t_void_p, ctypes.POINTER(ggml.ggml_tensor))
    t = t_ptr.contents
    if ask:
        name = t.name.decode("utf-8")
        did_match = False
        if match := re.match(r"inp_embd", name):
            cb_data.type = 0
            cb_data.layer = 0
            return not (cb_data.type in skip_types)
        elif match := re.match(r"kqv_out-(\d+)", name):
            cb_data.type = 1
            cb_data.layer = int(match.group(1)) + 1
            return (not (cb_data.type in skip_types)) and (cb_data.layer in target_layers_attn)
        elif match := re.match(r"ffn_out-(\d+)", name):
            cb_data.type = 2
            cb_data.layer = int(match.group(1)) + 1
            return (not (cb_data.type in skip_types)) and (cb_data.layer in target_layers_ffn)
        return False
    else:
        # Get tensor data
        buffer_ptr = ctypes.cast(cb_data.buffer, ctypes.c_void_p)
        ggml.ggml_backend_tensor_get(t_ptr, buffer_ptr, 0, t.ne[0] * 4)
        tensor = c_array_to_tensor(cb_data.buffer, (1, t.ne[0]), torch.float32)
        # Orthogonalize with correct direction
        if cb_data.type == 0:
            tensor = orthogonalize_matrix(tensor, direction_tok, amount) #direction_tok
        if cb_data.type == 1:
            tensor = orthogonalize_matrix(tensor, direction_attn[cb_data.layer - 1], amount)
        if cb_data.type == 2:
            tensor = orthogonalize_matrix(tensor, direction_ffn[cb_data.layer - 1], amount)
        # Set tensor data
        ggml.ggml_backend_tensor_set(t_ptr, tensor.numpy().ctypes.data, 0, t.ne[0] * 4)
        # Returning false stops graph in it's tracks without error
        return True
    # return True to request data next callback, false to skip, ask will be False when returning data from a request
    return False

c_hidden_states_eval_callback = ctypes.CFUNCTYPE(
    ctypes.c_bool, ctypes.c_void_p, ctypes.c_bool, ctypes.c_void_p
)(hidden_states_eval_callback)

def model_generate_hidden_states(model, context, batch, n_past, toks, buffer): #, direction):
    # Set callback vars
    callback_data.buffer = buffer
    #callback_data.direction = direction
    # Clear cache per sample instruction
    #llama_cpp.llama_kv_cache_clear(context)
    # Token count
    n_tokens = len(toks)
    # Fill batch
    batch.n_tokens = n_tokens
    for i in range(n_tokens):
        batch.token[i] = toks[i]
        batch.pos[i] = n_past + i
        batch.seq_id[i][0] = 0
        batch.n_seq_id[i] = 1
        batch.logits[i] = False
    batch.logits[n_tokens - 1] = True
    # Decode batch
    result = llama_cpp.llama_decode(context, batch)
    if result == 1:
        print("decode warning")
    elif result < 0:
        print("decode error")

def model_token_to_piece(model, token) -> str:
    size = 32
    buffer = (ctypes.c_char * size)()
    n = llama_cpp.llama_token_to_piece(model, llama_cpp.llama_token(token), buffer, size, 0, True)
    return buffer[:n].decode("utf-8")

# Clear memory of past model usage
model = None
gc.collect()

# Load model
model = model_load(model_path)
n_embd = llama_cpp.llama_n_embd(model)

toks = model_tokenize_chat(model, role="user", content=user_prompt, add_assistant=True)

#toks = [toks[0]]

# Create context
context_params = llama_cpp.llama_context_default_params()
n_threads = multiprocessing.cpu_count()
context_params.n_threads = n_threads
context_params.n_threads_batch = n_threads
context_params.seed  = 1337
context_params.cb_eval = c_hidden_states_eval_callback
context_params.cb_eval_user_data = ctypes.cast(ctypes.pointer(callback_data), ctypes.c_void_p)
context = llama_cpp.llama_new_context_with_model(model, context_params)

# Create batch
batch = llama_cpp.llama_batch_init(context_params.n_batch, 0, context_params.n_ctx)

# Create ctypes float direction
buffer_n_bytes = llama_cpp.llama_n_embd(model) * 4
buffer = ctypes.cast(ctypes.create_string_buffer(buffer_n_bytes), ctypes.POINTER(ctypes.c_float))

# Generate response
# Input tokens
n_past = 0
n_toks = len(toks)
for tok in toks:
    print(model_token_to_piece(model, tok), end="", flush=True)
    model_generate_hidden_states(model, context, batch, n_past, [tok], buffer)
    n_past += 1
# Output tokens (simple greedy)
n_generated = 0
is_generating = True
while is_generating:
    # Sample token
    logits = llama_cpp.llama_get_logits(context)
    n_vocab = llama_cpp.llama_n_vocab(model)
    data_array = (llama_cpp.llama_token_data * n_vocab)(
        *[llama_cpp.llama_token_data(token_id, logits[token_id], 0.0) for token_id in range(n_vocab)]
    )
    candidates = ctypes.pointer(llama_cpp.llama_token_data_array(data_array, len(data_array), False))
    probs = llama_cpp.llama_sample_softmax(context, candidates)
    tok = llama_cpp.llama_sample_token_greedy(context, candidates)
    # Check for stop tokens
    if llama_cpp.llama_token_is_eog(model, tok):
        is_generating = False
        break
    # Print token and generate another if needed
    print(model_token_to_piece(model, tok), end="", flush=True)
    n_generated += 1
    if n_generated >= n_max_tokens:
        is_generating = False
        break
    model_generate_hidden_states(model, context, batch, n_past, [tok], buffer)
    n_past += 1

# Free batch, model, context, and backend
llama_cpp.llama_batch_free(batch)
llama_cpp.llama_free(context)
llama_cpp.llama_free_model(model)
llama_cpp.llama_backend_free()

# Clean-up
model = None
context = None
gc.collect()

# Optional: Remove temporary harmful and harmless hidden state files

In [ ]:
#%cd /kaggle/working
#!rm -r ./harmful_states
#!rm -r ./harmless_states

# Download/modify/upload individual safetensors files separately to save memory

To save space in kaggle, I will download each split separately and patch it, then upload it to my own repo.

All of the smaller files will be uploaded as a folder.

Be sure to change the repo to your newly created huggingface repo and set all your kaggle secrets for reading and writing to hf!

There is some basic code to check and resume progress if something fails during the process. Not perfect, but helpful.

In [1]:
!rm /kaggle/working/upload_progress.pt

In [ ]:
%cd /kaggle/working

import os
import re
import gc
gc.collect()

from safetensors import safe_open
from safetensors.torch import save_file
from typing import Optional, Tuple

import einops
import jaxtyping
import torch

from huggingface_hub import hf_hub_download
from huggingface_hub import upload_folder
from huggingface_hub import upload_file

from transformers import AutoConfig

working_dir = "/kaggle/working"
local_repo_dir = working_dir + "/" + "Yi-1.5-34B-Chat"

download_repo = "01-ai/Yi-1.5-34B-Chat"
upload_repo = "byroneverson/Yi-1.5-34B-Chat-abliterated"

temp_dir = "/kaggle/temp"

# Make sure safetensors count matches the actual count for the model you are modifying
safetensors_count = 15

# Target layers
target_layer_tok = 26
target_layers_attn = [21, 26]
target_layers_ffn = [24, 27]

# Load feature direction
direction_tok = torch.load(local_repo_dir + "/" + "direction_ffn.pt", weights_only=True)[target_layer_tok - 1].to(torch.float32)
direction_attn = torch.load(local_repo_dir + "/" + "direction_attn.pt", weights_only=True).to(torch.float32)
direction_ffn = torch.load(local_repo_dir + "/" + "direction_ffn.pt", weights_only=True).to(torch.float32)

# HF
from kaggle_secrets import UserSecretsClient

user_secrets = UserSecretsClient()
read_token = user_secrets.get_secret("hf_read")
write_token = user_secrets.get_secret("hf_write")

# Download necessary files
try:
    for filename in ["config.json", 
                     "generation_config.json",
                     "model.safetensors.index.json", 
                     "special_tokens_map.json", 
                     "tokenizer.json", 
                     "tokenizer.model", 
                     "tokenizer_config.json",
                     "NOTICE"]:
        hf_hub_download(repo_id=download_repo, filename=filename, local_dir=local_repo_dir, use_auth_token=read_token)
except Exception as e:
    print(f"Error downloading {filename}: {e}")

# Upload smaller files first
try:
    upload_folder(folder_path=local_repo_dir, repo_id=upload_repo, token=write_token)
except Exception as e:
    print(f"Error uploading folder: {e}")

# Load model config and refusal direction
config = AutoConfig.from_pretrained(local_repo_dir, local_files_only=True, trust_remote_code=True)

def orthogonalize_matrix(matrix: jaxtyping.Float[torch.Tensor, "... d"], 
                        direction: jaxtyping.Float[torch.Tensor, "d"]) -> jaxtyping.Float[torch.Tensor, "... d"]:
    proj = einops.einsum(matrix, direction.view(-1, 1), "... d, d single -> ... single") * direction
    return matrix - proj

def load_safetensors_file(file_path):
    """Loads a single safetensors file into a dictionary of tensors.
    Args:
        file_path (str): Path to the safetensors file.
    Returns:
        dict: A dictionary containing the loaded tensors.
    """
    tensors = {}
    with safe_open(file_path, framework="pt", device="cpu") as f:
        #print(f.metadata())
        for key in f.keys():
            tensors[key] = f.get_tensor(key)
    return tensors

# Check for upload progress, if none create one
progress = None
progress_filename = "/kaggle/working/upload_progress.pt"
if os.path.isfile(progress_filename):
    progress = torch.load(progress_filename, weights_only=True)
else:
    progress = torch.tensor([0, 0])
    torch.save(progress, progress_filename)

start_index = progress[0]
device = direction_ffn.device
# TODO: Add in skip start and end layers logic
#       I forgot to in v1.0 but the abliterated output model still worked great so I didn't even notice
for idx in range(start_index, safetensors_count):
    gc.collect()
    
    # Current .safetensors
    filename = "model-" + str(idx + 1).zfill(5) + "-of-" + str(safetensors_count).zfill(5) + ".safetensors"
    print(filename)
    
    # Local file path
    file_path = temp_dir + "/" + filename
    
    # Check if we need to skip processing this file and just upload it
    skip_processing = False
    
    # Download file 
    if os.path.isfile(file_path):
        skip_processing = True if progress[1] >= 1 else False
    else:
        hf_hub_download(repo_id=download_repo, filename=filename, local_dir=temp_dir, use_auth_token=read_token)
    
    if not skip_processing:
        # Load local file
        tensors = load_safetensors_file(file_path)

        for tensor in tensors:
            
            # Get current layer number (not layer index)
            layer = -1
            match = re.search(r"layers\.(\d+)\.", tensor)
            if match:
                layer = int(match.group(1)) + 1

            # tok_embeddings
            if ".embed_tokens.weight" in tensor:
                if target_layer_tok:
                    direction = direction_tok
                    print("• " + tensor)
                    dtype = tensors[tensor].dtype
                    t = tensors[tensor].to(torch.float32).to(device)
                    tensors[tensor].copy_(orthogonalize_matrix(t, direction).to(dtype))
                    t = []

            # attention.wo
            if ".self_attn.o_proj.weight" in tensor:
                if layer in target_layers_attn:
                    direction = direction_attn[layer - 1]
                    print("• " + tensor)
                    dtype = tensors[tensor].dtype
                    t = tensors[tensor].to(torch.float32).to(device)
                    t_rearranged = einops.rearrange(t, "m (n h) -> n h m", n=config.num_attention_heads).to(device)
                    t_orthogonalized = orthogonalize_matrix(t_rearranged, direction)
                    t_rearranged = einops.rearrange(t_orthogonalized, "n h m -> m (n h)", n=config.num_attention_heads)
                    tensors[tensor].copy_(t_rearranged.to(dtype))
                    t = []
                    t_rearranged = []
                    t_orthogonalized = []

            # feed_forward.w2
            if ".mlp.down_proj.weight" in tensor:
                if layer in target_layers_ffn:
                    direction = direction_ffn[layer - 1]
                    print("• " + tensor)
                    dtype = tensors[tensor].dtype
                    t = tensors[tensor].to(torch.float32).to(device)
                    t_transposed = t.T.to(device)
                    t_orthogonalized = orthogonalize_matrix(t_transposed, direction)
                    t_transposed = t_orthogonalized.T
                    tensors[tensor].copy_(t_transposed.to(dtype))
                    t = []
                    t_transposed = []
                    t_orthogonalized = []

        # Save file
        save_file(tensors, file_path, metadata={'format': 'pt'})

        # Save progress after processing
        progress[1] = 1
        torch.save(progress, progress_filename)
        
    # Upload file if we need to
    skip_upload = True if progress[1] >= 2 else False
    if not skip_upload:
        # Upload file to your repo
        upload_file(path_or_fileobj=file_path, path_in_repo=filename, repo_id=upload_repo, token=write_token)
        
        # Save progress after processing
        progress[1] = 2
        torch.save(progress, progress_filename)

    # Try to remove file if it still exists
    import os
    if os.path.exists(file_path):
        os.remove(file_path)
    else:
        print("Remove error: The file does not exist")
        
    # Save progress for next file
    progress[0] = idx + 1
    progress[1] = 0
    torch.save(progress, progress_filename)

# Delete progress file
!rm /kaggle/working/upload_progress.pt

# Patching done
print("Done!")


# Use GGUF My Repo space on HF to convert abliterated model to GGUF

# Test in your favorite llama.cpp or GGUF environment

# Convert a split .safetensors model directly into quantized split gguf

1. Split counts should match, so the tensors that are in the first safetensors should match the first gguf split.
2. Metadata will be stored in first of gguf split.
3. This process does not need to create an f16 gguf first. Simply input the hf split safetensors model and output a split quant gguf.
4. Merging this split model is the same as usual, can use the normal gguf-split tool to perform merges.

In [ ]:
import llama_cpp
import ggml
import torch

# Set safetensors count
# TODO: Detect this from safetensors files
safetensors_count = 15

# Should we generate the gguf as well?
gguf_generate = True
# Quantization type
gguf_ggml_type = "q4_k_m"

# Write metadata to first gguf
def gguf_write_metadata():
    # TODO
    return

# Convert individual safetensor split file to gguf split file, tensors by tensor
def gguf_convert_safetensor(input_path, output_path);
    return

# TODO: Merge this into above step for converting to gguf during safetensors abliteration
for i in range(safetensors_count):
    # Iterate safetensors
    
    # For first safetensors, write metadata
    
    



# Optional: Download 

In [ ]:
if oauth_token.token is None:
        raise ValueError("You must be logged in to use GGUF-my-repo")
    model_name = model_id.split('/')[-1]
    fp16 = f"{model_name}.fp16.gguf"

    try:
        api = HfApi(token=oauth_token.token)

        dl_pattern = ["*.md", "*.json", "*.model"]

        pattern = (
            "*.safetensors"
            if any(
                file.path.endswith(".safetensors")
                for file in api.list_repo_tree(
                    repo_id=model_id,
                    recursive=True,
                )
            )
            else "*.bin"
        )

        dl_pattern += pattern

        api.snapshot_download(repo_id=model_id, local_dir=model_name, local_dir_use_symlinks=False, allow_patterns=dl_pattern)
        print("Model downloaded successfully!")
        print(f"Current working directory: {os.getcwd()}")
        print(f"Model directory contents: {os.listdir(model_name)}")

        conversion_script = "convert_hf_to_gguf.py"
        fp16_conversion = f"python llama.cpp/{conversion_script} {model_name} --outtype f16 --outfile {fp16}"
        result = subprocess.run(fp16_conversion, shell=True, capture_output=True)
        print(result)
        if result.returncode != 0:
            raise Exception(f"Error converting to fp16: {result.stderr}")
        print("Model converted to fp16 successfully!")
        print(f"Converted model path: {fp16}")

        imatrix_path = "llama.cpp/imatrix.dat"

        if use_imatrix:
            if train_data_file:
                train_data_path = train_data_file.name
            else:
                train_data_path = "groups_merged.txt" #fallback calibration dataset

            print(f"Training data file path: {train_data_path}")

            if not os.path.isfile(train_data_path):
                raise Exception(f"Training data file not found: {train_data_path}")

            generate_importance_matrix(fp16, train_data_path)
        else:
            print("Not using imatrix quantization.")
        username = whoami(oauth_token.token)["name"]
        quantized_gguf_name = f"{model_name.lower()}-{imatrix_q_method.lower()}-imat.gguf" if use_imatrix else f"{model_name.lower()}-{q_method.lower()}.gguf"
        quantized_gguf_path = quantized_gguf_name
        if use_imatrix:
            quantise_ggml = f"./llama.cpp/llama-quantize --imatrix {imatrix_path} {fp16} {quantized_gguf_path} {imatrix_q_method}"
        else:
            quantise_ggml = f"./llama.cpp/llama-quantize {fp16} {quantized_gguf_path} {q_method}"
        result = subprocess.run(quantise_ggml, shell=True, capture_output=True)
        if result.returncode != 0:
            raise Exception(f"Error quantizing: {result.stderr}")
        print(f"Quantized successfully with {imatrix_q_method if use_imatrix else q_method} option!")
        print(f"Quantized model path: {quantized_gguf_path}")

        # Create empty repo
        new_repo_url = api.create_repo(repo_id=f"{username}/{model_name}-{imatrix_q_method if use_imatrix else q_method}-GGUF", exist_ok=True, private=private_repo)
        new_repo_id = new_repo_url.repo_id
        print("Repo created successfully!", new_repo_url)

        try:
            card = ModelCard.load(model_id, token=oauth_token.token)
        except:
            card = ModelCard("")
        if card.data.tags is None:
            card.data.tags = []
        card.data.tags.append("llama-cpp")
        card.data.tags.append("gguf-my-repo")
        card.data.base_model = model_id
        card.text = dedent(
            f"""
            # {new_repo_id}
            This model was converted to GGUF format from [`{model_id}`](https://huggingface.co/{model_id}) using llama.cpp via the ggml.ai's [GGUF-my-repo](https://huggingface.co/spaces/ggml-org/gguf-my-repo) space.
            Refer to the [original model card](https://huggingface.co/{model_id}) for more details on the model.
            
            ## Use with llama.cpp
            Install llama.cpp through brew (works on Mac and Linux)
            
            ```bash
            brew install llama.cpp
            
            ```
            Invoke the llama.cpp server or the CLI.
            
            ### CLI:
            ```bash
            llama-cli --hf-repo {new_repo_id} --hf-file {quantized_gguf_name} -p "The meaning to life and the universe is"
            ```
            
            ### Server:
            ```bash
            llama-server --hf-repo {new_repo_id} --hf-file {quantized_gguf_name} -c 2048
            ```
            
            Note: You can also use this checkpoint directly through the [usage steps](https://github.com/ggerganov/llama.cpp?tab=readme-ov-file#usage) listed in the Llama.cpp repo as well.
            Step 1: Clone llama.cpp from GitHub.
            ```
            git clone https://github.com/ggerganov/llama.cpp
            ```
            Step 2: Move into the llama.cpp folder and build it with `LLAMA_CURL=1` flag along with other hardware-specific flags (for ex: LLAMA_CUDA=1 for Nvidia GPUs on Linux).
            ```
            cd llama.cpp && LLAMA_CURL=1 make
            ```
            Step 3: Run inference through the main binary.
            ```
            ./llama-cli --hf-repo {new_repo_id} --hf-file {quantized_gguf_name} -p "The meaning to life and the universe is"
            ```
            or 
            ```
            ./llama-server --hf-repo {new_repo_id} --hf-file {quantized_gguf_name} -c 2048
            ```
            """
        )
        card.save(f"README.md")

        if split_model:
            split_upload_model(quantized_gguf_path, new_repo_id, oauth_token, split_max_tensors, split_max_size)
        else:
            try:
                print(f"Uploading quantized model: {quantized_gguf_path}")
                api.upload_file(
                    path_or_fileobj=quantized_gguf_path,
                    path_in_repo=quantized_gguf_name,
                    repo_id=new_repo_id,
                )
            except Exception as e:
                raise Exception(f"Error uploading quantized model: {e}")
        
        
        imatrix_path = "llama.cpp/imatrix.dat"
        if os.path.isfile(imatrix_path):
            try:
                print(f"Uploading imatrix.dat: {imatrix_path}")
                api.upload_file(
                    path_or_fileobj=imatrix_path,
                    path_in_repo="imatrix.dat",
                    repo_id=new_repo_id,
                )
            except Exception as e:
                raise Exception(f"Error uploading imatrix.dat: {e}")

        api.upload_file(
            path_or_fileobj=f"README.md",
            path_in_repo=f"README.md",
            repo_id=new_repo_id,
        )
        print(f"Uploaded successfully with {imatrix_q_method if use_imatrix else q_method} option!")

        return (
            f'Find your repo <a href=\'{new_repo_url}\' target="_blank" style="text-decoration:underline">here</a>',
            "llama.png",
        )
    except Exception as e:
        return (f"Error: {e}", "error.png")
    finally:
        shutil.rmtree(model_name, ignore_errors=True)
        print("Folder cleaned up successfully!")